In [ ]:
#!pip install --upgrade tensorflow
#!pip install scikit-learn
#!pip install pandas
#!pip install keras==2.14.0

In [ ]:
import numpy as np
import pandas as pd
import os
import string
import re
from string import digits
from sklearn.utils import shuffle
from sklearn.model_selection import train_test_split
import tensorflow as tf
from tensorflow.keras.layers import Input, LSTM, Embedding, Dense
from tensorflow.keras.models import Model

In [ ]:
# Reading csv
lines = pd.read_csv("Hindi_English_Truncated_Corpus.csv", encoding='utf-8')
lines.head()

In [ ]:
lines['source'].value_counts()

lines = lines[lines['source'] == 'ted']

print(lines.head(20))

In [ ]:
pd.isnull(lines).sum()

lines = lines[~pd.isnull(lines['english_sentence'])]

lines.drop_duplicates(inplace=True)

lines = lines.sample(n=25000, random_state=42)
print(lines.shape)

In [ ]:
# Lowercase all characters
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.lower())
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.lower())

# Remove quotes
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: re.sub("'", '', x))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub("'", '', x))

exclude = set(string.punctuation)  # Set of all special characters
# Remove all the special characters
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: ''.join(ch for ch in x if ch not in exclude))

# Remove all numbers from text
remove_digits = str.maketrans('', '', digits)
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.translate(remove_digits))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.translate(remove_digits))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub("[२३०८१५७९४६]", "", x))

# Remove extra spaces
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: x.strip())
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: x.strip())
lines['english_sentence'] = lines['english_sentence'].apply(lambda x: re.sub(" +", " ", x))
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: re.sub(" +", " ", x))

# Add start and end tokens to target sequences
lines['hindi_sentence'] = lines['hindi_sentence'].apply(lambda x: 'START_ ' + x + ' _END')
print(lines.head())

# Get English and Hindi Vocabulary
all_eng_words = set()
for eng in lines['english_sentence']:
    for word in eng.split():
        if word not in all_eng_words:
            all_eng_words.add(word)

all_hindi_words = set()
for hin in lines['hindi_sentence']:
    for word in hin.split():
        if word not in all_hindi_words:
            all_hindi_words.add(word)

print("all_eng_words: ", len(all_eng_words))
print("all_hindi_words: ", len(all_hindi_words))

In [ ]:
lines['length_eng_sentence'] = lines['english_sentence'].apply(lambda x: len(x.split(" ")))
lines['length_hin_sentence'] = lines['hindi_sentence'].apply(lambda x: len(x.split(" ")))
print(lines.head())

In [ ]:
lines = lines[lines['length_eng_sentence'] <= 20]
lines = lines[lines['length_hin_sentence'] <= 20]
print(lines.shape)

In [ ]:
print("maximum length of Hindi Sentence ", max(lines['length_hin_sentence']))
print("maximum length of English Sentence ", max(lines['length_eng_sentence']))

In [ ]:
max_length_src = max(lines['length_hin_sentence'])
max_length_tar = max(lines['length_eng_sentence'])

input_words = sorted(list(all_eng_words))
target_words = sorted(list(all_hindi_words))
num_encoder_tokens = len(all_eng_words)
num_decoder_tokens = len(all_hindi_words)
num_encoder_tokens, num_decoder_tokens

num_decoder_tokens += 1  # for zero padding

input_token_index = dict([(word, i + 1) for i, word in enumerate(input_words)])
target_token_index = dict([(word, i + 1) for i, word in enumerate(target_words)])

reverse_input_char_index = dict((i, word) for word, i in input_token_index.items())
reverse_target_char_index = dict((i, word) for word, i in target_token_index.items())

lines = shuffle(lines)
print(lines.head(10))

In [ ]:
X, y = lines['english_sentence'], lines['hindi_sentence']
X_train, X_test, y_train, y_test = train_test_split(X, y, test_size=0.2, random_state=42)
print(X_train.shape,'\n' X_test.shape)

In [ ]:
X_train.to_pickle('X_train.pkl')
X_test.to_pickle('X_test.pkl')

In [ ]:
num_encoder_tokens = len(input_token_index) + 1
num_decoder_tokens = len(target_token_index) + 1

if 0 not in input_token_index.values():
    max_index = max(input_token_index.values())
    input_token_index['<PAD>'] = max_index + 1
    num_encoder_tokens += 1

# Define generate_batch function here
def generate_batch(X=X_train, y=y_train, batch_size=128):
    while True:
        for j in range(0, len(X), batch_size):
            encoder_input_data = np.zeros((batch_size, max_length_src), dtype='float32')
            decoder_input_data = np.zeros((batch_size, max_length_tar), dtype='float32')
            decoder_target_data = np.zeros((batch_size, max_length_tar, num_decoder_tokens), dtype='float32')
            for i, (input_text, target_text) in enumerate(zip(X[j:j + batch_size], y[j:j + batch_size])):
                for t, word in enumerate(input_text.split()):
                    encoder_input_data[i, t] = input_token_index.get(word, input_token_index['<PAD>'])

                for t, word in enumerate(target_text.split()):
                    if t < len(target_text.split()) - 1:
                        decoder_input_data[i, t] = target_token_index.get(word, 0)
                    if t > 0:
                        decoder_target_data[i, t - 1, target_token_index.get(word, 0)] = 1.
            yield ([encoder_input_data, decoder_input_data], decoder_target_data)

latent_dim = 300

encoder_inputs = Input(shape=(None,))
enc_emb = Embedding(num_encoder_tokens, latent_dim, mask_zero=True)(encoder_inputs)
encoder_lstm = LSTM(latent_dim, return_state=True)
encoder_outputs, state_h, state_c = encoder_lstm(enc_emb)
encoder_states = [state_h, state_c]

decoder_inputs = Input(shape=(None,))
dec_emb_layer = Embedding(num_decoder_tokens, latent_dim, mask_zero=True)
dec_emb = dec_emb_layer(decoder_inputs)
decoder_lstm = LSTM(latent_dim, return_sequences=True, return_state=True)
decoder_outputs, _, _ = decoder_lstm(dec_emb, initial_state=encoder_states)
decoder_dense = Dense(num_decoder_tokens, activation='softmax')
decoder_outputs = decoder_dense(decoder_outputs)

model = Model([encoder_inputs, decoder_inputs], decoder_outputs)
model.compile(optimizer='adam', loss='categorical_crossentropy', metrics=['accuracy'])

model.summary()

train_samples = len(X_train)
val_samples = len(X_test)
batch_size = 128
epochs = 100
model.fit(x=generate_batch(X_train, y_train, batch_size=batch_size),
          steps_per_epoch=train_samples // batch_size,
          epochs=epochs,
          validation_data=generate_batch(X_test, y_test, batch_size=batch_size),
          validation_steps=val_samples // batch_size)

In [ ]:
model.save_weights('nmt_weights.h5')
model.load_weights('nmt_weights.h5')

In [ ]:
encoder_model = Model(encoder_inputs, encoder_states)

decoder_state_input_h = Input(shape=(latent_dim,))
decoder_state_input_c = Input(shape=(latent_dim,))
decoder_states_inputs = [decoder_state_input_h, decoder_state_input_c]

dec_emb2 = dec_emb_layer(decoder_inputs)
decoder_outputs2, state_h2, state_c2 = decoder_lstm(dec_emb2, initial_state=decoder_states_inputs)
decoder_states2 = [state_h2, state_c2]
decoder_outputs2 = decoder_dense(decoder_outputs2)

decoder_model = Model(
    [decoder_inputs] + decoder_states_inputs,
    [decoder_outputs2] + decoder_states2)


def decode_sequence(input_seq):
    states_value = encoder_model.predict(input_seq)
    target_seq = np.zeros((1, 1))
    target_seq[0, 0] = target_token_index['START_']

    stop_condition = False
    decoded_sentence = ''
    while not stop_condition:
        output_tokens, h, c = decoder_model.predict([target_seq] + states_value)

        sampled_token_index = np.argmax(output_tokens[0, -1, :])
        sampled_char = reverse_target_char_index[sampled_token_index]
        decoded_sentence += ' ' + sampled_char

        if (sampled_char == '_END' or len(decoded_sentence) > 50):
            stop_condition = True

        target_seq = np.zeros((1, 1))
        target_seq[0, 0] = sampled_token_index

        states_value = [h, c]

    return decoded_sentence

In [ ]:
train_gen = generate_batch(X_train, y_train, batch_size=1)
k = -1

k += 1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k + 1].values[0])
print('Actual Hindi Translation:', y_train[k:k + 1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

k+=1
(input_seq, actual_output), _ = next(train_gen)
decoded_sentence = decode_sequence(input_seq)
print('Input English sentence:', X_train[k:k+1].values[0])
print('Actual Hindi Translation:', y_train[k:k+1].values[0][6:-4])
print('Predicted Hindi Translation:', decoded_sentence[:-4])

########################################################################################################################################################

In [ ]:
#!pip install nltk

In [19]:
import nltk
from tensorflow.keras.preprocessing.sequence import pad_sequences

# Calculate cross-entropy score
test_gen = generate_batch(X_test, y_test, batch_size=1)
loss, accuracy = model.evaluate(test_gen, steps=len(X_test))

print(f"Cross-entropy Loss: {loss}")
print(f"Accuracy: {accuracy}")

4955/4955 [==============================] - 41s 8ms/step - loss: 10.1642 - accuracy: 0.2140
Cross-entropy Loss: 10.164168357849121
Accuracy: 0.2140292376279831


In [22]:
from tqdm import tqdm
from nltk.translate.bleu_score import SmoothingFunction

def get_reference_and_candidate_sequences(X_test, y_test):
    predicted_sequences = []
    references = []

    for input_sentence, target_sentence in tqdm(zip(X_test, y_test), total=len(X_test)):
        input_sequence = []
        for word in input_sentence.split():
            if word in input_token_index:
                input_sequence.append(input_token_index[word])
            else:
                input_sequence.append(input_token_index['<PAD>'])

        input_sequence = pad_sequences([input_sequence], maxlen=max_length_src, padding='post')
        translated_seq = decode_sequence(input_sequence)
        translated_seq = translated_seq.split()
        predicted_sequences.append(translated_seq)

        references.append(target_sentence.split())

    return references, predicted_sequences

references, candidates = get_reference_and_candidate_sequences(X_test, y_test)

# Using SmoothingFunction to handle cases where there are zero n-gram overlaps
smoother = SmoothingFunction()
bleu_score = nltk.translate.bleu_score.corpus_bleu(references, candidates, smoothing_function=smoother.method1)
print(f"BLEU Score: {bleu_score}")


  0%|          | 0/4955 [00:00<?, ?it/s]

1/1 [==============================] - 0s 21ms/step


  0%|          | 1/4955 [00:00<36:47,  2.24it/s]

1/1 [==============================] - 0s 22ms/step


  0%|          | 2/4955 [00:01<48:26,  1.70it/s]

...

1/1 [==============================] - 0s 22ms/step


100%|█████████▉| 4954/4955 [50:23<00:00,  1.25it/s]

1/1 [==============================] - 0s 24ms/step


100%|██████████| 4955/4955 [50:24<00:00,  1.64it/s]


BLEU Score: 1.448486241324191e-05
